In [15]:
!pip3 install simpletransformers
!pip3 install transformers
!pip3 install datasets

In [41]:
from simpletransformers.classification import ClassificationModel
# from simpletransformers import 
# from transformers import AutoTokenizer, Trainer

train_args = {
    'learning_rate': 1e-5,
    'max_seq_length': 512,
    'overwrite_output_dir': True,
    'reprocess_input_data': False,
    'train_batch_size': 4,
    'num_train_epochs': 4,
    'gradient_accumulation_steps': 2,
    'no_cache': True,
    'use_cached_eval_features': False,
    'save_model_every_epoch': False,
    'output_dir': "output",
    'eval_batch_size': 8,
    'fp16_opt_level': 'O2'
}

model = ClassificationModel('roberta', 'a-ware/roberta-large-squadv2', args=train_args, num_labels=2)
tokenizer = model.tokenizer

Some weights of the model checkpoint at a-ware/roberta-large-squadv2 were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'qa_outputs.bias', 'qa_outputs.weight', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at a-ware/roberta-large-squadv2 and are newly initialized: ['classifier.out_proj.bias', 'classifier.dense.weight', 'classifier.out_proj.weight', 'classifier.dense.bias']

In [124]:
predictions, raw_outputs = model.predict([["my dog is an year old. he loves to go into the rain", "how old is my dog ?"]])
print(predictions)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

[0]


In [125]:
predictions[0] == 0

True

In [93]:
import pandas as pd


def preprocess_function(data):
    labels = []
    
    for i in range(len(data["answers"])):
        if data["answers"][i]["text"] == ['']:
            labels.append(0.0)
        else:
            labels.append(1.0)
    zipped = list(zip(data["contexts"], data["questions"], labels))
    return pd.DataFrame(zipped, columns=['text_a', 'text_b', 'labels'])

In [44]:
import pandas as pd
import numpy as np

def get_annotated_empty(dfs):
    answers = []
    questions = []
    contexts = []

    for df in dfs:
        for i in range(len(df)-1):
            if len(df.iloc[i]["Eligibility & Requirements"].strip()) == 0:
                question = "What are the Eligibility & Requirement criteria?"
                questions.append(question)
                ans = ""
                index = 0
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                contexts.append(dfs[0].iloc[i]["Text"])

            if len(df.iloc[i]["Documents"].strip()) == 0:
                question = "What are the required documents?"
                questions.append(question)
                ans = ""
                index = 0
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                contexts.append(dfs[0].iloc[i]["Text"])

            if len(df.iloc[i]["Services"].strip()) == 0:
                question = "What are the provided services?"
                questions.append(question)
                ans = ""
                index = 0
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                contexts.append(dfs[0].iloc[i]["Text"])

            if len(df.iloc[i]["Admission Process"].strip()) == 0:
                question = "What is the admission process?"
                questions.append(question)
                ans = ""
                index = 0
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                contexts.append(dfs[0].iloc[i]["Text"])

            if len(df.iloc[i]["Duration of Stay"].strip()) == 0:
                question = "How long can one stay?"
                questions.append(question)
                ans = ""
                index = 0
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                contexts.append(dfs[0].iloc[i]["Text"])

    return answers, questions, contexts


def get_annotated_data(dfs):
    answers = []
    questions = []
    contexts = []
    for df in dfs:
        for i in range(len(df)-1):
            if len(df.iloc[i]["Eligibility & Requirements"].strip()) > 0:
                question = "What are the Eligibility & Requirement criteria?"
                questions.append(question)
                ans = df.iloc[i]["Eligibility & Requirements"]
                index = df.iloc[i]["Text"].find(ans)
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                
                contexts.append(df.iloc[i]["Text"])

            if len(df.iloc[i]["Documents"].strip()) > 0:
                question = "What are the required documents?"
                questions.append(question)
                ans = df.iloc[i]["Documents"]
                index = df.iloc[i]["Text"].find(ans)
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                
                contexts.append(df.iloc[i]["Text"])

            if len(df.iloc[i]["Services"].strip()) > 0:
                question = "What are the provided services?"
                questions.append(question)
                ans = df.iloc[i]["Services"]
                index = df.iloc[i]["Text"].find(ans)
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                
                contexts.append(df.iloc[i]["Text"])

            if len(df.iloc[i]["Admission Process"].strip()) > 0:
                question = "What is the admission process?"
                questions.append(question)
                ans = df.iloc[i]["Admission Process"]
                index = df.iloc[i]["Text"].find(ans)
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                
                contexts.append(df.iloc[i]["Text"])

            if len(df.iloc[i]["Duration of Stay"].strip()) > 0:
                question = "How long can one stay?"
                questions.append(question)
                ans = df.iloc[i]["Duration of Stay"]
                index = df.iloc[i]["Text"].find(ans)
                answers.append({
                    "answer_start": [index],
                    "text": [ans]
                })
                
                contexts.append(df.iloc[i]["Text"])

    return answers, questions, contexts

In [94]:
from datasets import Dataset

# training set
df_1 = pd.read_excel("annotator_1.xlsx", keep_default_na=False)
df_2 = pd.read_excel("annotator_2.xlsx", keep_default_na=False)
df_3 = pd.read_excel("annotator_3.xlsx", keep_default_na=False)
train_ans, train_ques, train_text = get_annotated_data([df_1[100:], df_2[200:], df_3[200:]])
train_ans_e, train_ques_e, train_text_e = get_annotated_empty([df_1[100:], df_2[200:], df_3[200:]])
train_ans = np.concatenate((train_ans, train_ans_e))
train_ques = np.concatenate((train_ques, train_ques_e))
train_text = np.concatenate((train_text, train_text_e))
data = {
    "answers": train_ans,
    "questions": train_ques,
    "contexts": train_text
}

tokenized_train = preprocess_function(data)

In [95]:
tokenized_train

text_a  \
0      Offers emergency shelter for youth 12 to 17 y...   
1      Offers emergency shelter for youth 12 to 17 y...   
2      Offers emergency shelter for youth 12 to 17 y...   
3      Transitional housing for adults with mental c...   
4      Transitional housing for adults with mental c...   
...                                                 ...   
5010   Women and children. One intact family unit. O...   
5011   Women and children. One intact family unit. O...   
5012   Provides a halfway house for men. Rehab and r...   
5013   Provides a halfway house for men. Rehab and r...   
5014   Provides a halfway house for men. Rehab and r...   

                                                text_b  labels  
0     What are the Eligibility & Requirement criteria?     1.0  
1                      What are the provided services?     1.0  
2                               How long can one stay?     1.0  
3     What are the Eligibility & Requirement criteria?     1.0  
4                       What is the admission process?     1.0  
...                                                ...     ...  
5010                    What is the admission process?     0.0  
5011                            How long can one stay?     0.0  
5012                  What are the required documents?     0.0  
5013                    What is the admission process?     0.0  
5014                            How long can one stay?     0.0  

[5015 rows x 3 columns]

In [96]:
# validation
df_validate = pd.read_excel("gold.xlsx", keep_default_na=False)
val_ans, val_ques, val_text = get_annotated_data([df_validate[50:]])
print(len(val_ans))
val_ans_e, val_ques_e, val_text_e = get_annotated_empty([df_validate[50:]])
print(len(val_ans_e))
val_ans = np.concatenate((val_ans, val_ans_e))
val_ques = np.concatenate((val_ques, val_ques_e))
val_text = np.concatenate((val_text, val_text_e))
data = {
    "answers": val_ans,
    "questions": val_ques,
    "contexts": val_text
}

tokenized_eval = preprocess_function(data)

94
146


In [97]:
tokenized_eval

text_a  \
0     Provides a transitional shelter for abused an...   
1     Provides a transitional shelter for abused an...   
2     Provides a transitional shelter for abused an...   
3     Pathways of Hope offers a variety of programs...   
4     San Gabriel Valley Coordinated Entry System C...   
..                                                 ...   
235  Provides transitional housing for veterans. Of...   
236  Provides transitional housing for veterans. Of...   
237  The FOCUS/Disabilities Transitional Housing Pr...   
238  The FOCUS/Disabilities Transitional Housing Pr...   
239  The FOCUS/Disabilities Transitional Housing Pr...   

                                               text_b  labels  
0    What are the Eligibility & Requirement criteria?     1.0  
1                     What are the provided services?     1.0  
2                              How long can one stay?     1.0  
3                     What are the provided services?     1.0  
4                     What are the provided services?     1.0  
..                                                ...     ...  
235                  What are the required documents?     0.0  
236                            How long can one stay?     0.0  
237                  What are the required documents?     0.0  
238                    What is the admission process?     0.0  
239                            How long can one stay?     0.0  

[240 rows x 3 columns]

In [47]:
print(len(train_ans))
print(len(val_ans))

5015
240


In [98]:
model.train_model(train_df=tokenized_train, eval_df=tokenized_eval)

  0%|          | 0/5015 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:309: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/1254 [00:00<?, ?it/s]

Running Epoch 1 of 4:   0%|          | 0/1254 [00:00<?, ?it/s]

Running Epoch 2 of 4:   0%|          | 0/1254 [00:00<?, ?it/s]

Running Epoch 3 of 4:   0%|          | 0/1254 [00:00<?, ?it/s]

(2508, 0.41015036054961146)

In [100]:
import pickle

with open("roberta_classifier", "wb") as file:
    pickle.dump(model, file)

In [103]:
# test set
df_test = pd.read_excel("gold.xlsx", keep_default_na=False)
test_ans, test_ques, test_text = get_annotated_data([df_test[:50]])
print(len(test_ans))
test_ans_e, test_ques_e, test_text_e = get_annotated_empty([df_test[:50]])
print(len(test_ans_e))
test_ans = np.concatenate((test_ans, test_ans_e))
test_ques = np.concatenate((test_ques, test_ques_e))
test_text = np.concatenate((test_text, test_text_e))
data = {
    "answers": test_ans,
    "questions": test_ques,
    "contexts": test_text
}

test_set = preprocess_function(data)

140
105


In [126]:
from transformers import pipeline
import json

with open("2e-05_fine_roberta_3_epoch", "rb") as file:
    roberta_qa = pickle.load(file)

nlp = pipeline('question-answering', model=roberta_qa, tokenizer="deepset/roberta-base-squad2")

In [127]:
df = pd.read_excel("gold.xlsx", keep_default_na=False)
validate_set = df[:50]

# csv
gold = []
pred = {}

questions = [
    "What are the Eligibility & Requirement criteria?",
    "What are the required documents?",
    "What are the provided services?",
    "What is the admission process?",
    "How long can one stay?"
]

columns = ["Eligibility & Requirements", "Documents", "Services", "Admission Process", "Duration of Stay"]

for i in range(len(validate_set)):
    index = str(validate_set.iloc[i]["Index"])
    context = validate_set.iloc[i]["Text"]
    paragraph = {
        "context": context,
        "qas": []
    }

    for j in range(len(questions)):
        if j == j: # line to be used to select label
            predictions, raw_outputs = model.predict([[context, questions[j]]])
            if predictions[0] == 0:
                pred[index + "_" + str(j)] = ""
            else:
                # model query
                qa = {
                    "question": questions[j],
                    "context": context
                }
                answer = nlp(qa)
                pred[index + "_" + str(j)] = answer["answer"]

                # print(index + "_" + str(j), answer["answer"])
                # print(validate_set.iloc[i][columns[j]], "\n")

            # gold
            if len(validate_set.iloc[i][columns[j]].strip()) == 0:
                paragraph["qas"].append({
                    "question": questions[j],
                    "id": index + "_" + str(j),
                    "answers": [],
                    "is_impossible": True
                })

            else:
                if "###" in validate_set.iloc[i][columns[j]]:
                    multi_answers = validate_set.iloc[i][columns[j]].split("###")
                    answers = []
                    for ans in multi_answers:
                        answers.append({
                            "text": ans,
                            "answer_start": context.find(ans)
                        })
                else:
                    answers = [{
                        "text": validate_set.iloc[i][columns[j]],
                        "answer_start": context.find(validate_set.iloc[i][columns[j]])
                    }]

                paragraph["qas"].append({
                    "question": questions[j],
                    "id": index + "_" + str(j),
                    "answers": answers,
                    "is_impossible": False
                })

    gold.append(paragraph)

# write
gold = {
    "data": [
        {
            "title": "Homelessness",
            "paragraphs": gold
        }
    ]
}
with open("gold.json", "w") as file:
    file.writelines(json.dumps(gold))

with open("roberta_main_pred.json", "w") as file:
    file.writelines(json.dumps(pred))

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]